In [1]:
import apogee.tools.read as apread
import apogee.spec.plot as splot
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
Lambda = splot.apStarWavegrid()
import csv
import sys

In [2]:
def find_nearest(array,value):
    index = (np.abs(array-value)).argmin()
    #return array[index]
    return index

In [3]:
def Brackett_Equiv_Width(loc_id,twomass_id,j,EqW_array,emission_dict):
    
    #given a certain spec
    spec_header = apread.apStar(loc_id,twomass_id,ext=0,header=True)
    spec_noheader = apread.apStar(loc_id,twomass_id,ext=1,header=False)
    nvisits = spec_header[1]['NVISITS']
    vhelio = spec_header[1]['VHELIO']
    
    
    #Calculating Equivalent Width
    n=float((11+j)**2)
    c = 299792
    rydberg = 1.0973731568539*(10**7)
    electron = 9.10938356*(10**-31)
    nucleus = 1.672621898*(10**-27)
    fracryd = rydberg/(1+(electron/nucleus))
    
    
    vacuum = fracryd*((1./16.)-(1./n))
    lambda_obs = 1/vacuum
    calculated_point1 = lambda_obs*(1+(-vhelio/c))
    calculated_point2 = calculated_point1*(10**10)
    
#EqW Calculations for NVISITS = 1
    if nvisits == 1:
            
        spec = spec_noheader
    
        centerline = find_nearest(Lambda,calculated_point2)
        L1 = centerline - 135
        L2 = centerline - 90
        R1 = centerline + 90
        R2 = centerline + 135
            
        #generic continuum lines 35 elements wide 
        lsum= np.sum(spec[L1:L2])/ len(spec[L1:L2])
        rsum = np.sum(spec[R1:R2])/len(spec[R1:R2])
        Fc= (lsum+rsum)/2
        EqW=0
        
        if Fc!=0:
            for i in range(L2,centerline):
                left_area = (Lambda[i+1]-Lambda[i])*(spec[i+1]-Fc)-(1./2.)*(Lambda[i+1]-Lambda[i])*(spec[i+1]-spec[i])
                EqW += left_area
            for i in range(centerline,R1):
                right_area = (Lambda[i+1]-Lambda[i])*(spec[i]-Fc)-(1./2.)*(Lambda[i+1]-Lambda[i])*(spec[i]-spec[i+1])
                EqW += right_area
            EqW_rounded = round(EqW/Fc,5)
            EqW_array.append(EqW_rounded)
            
        if Fc==0:
            EqW_array.append(0)
    
#EqW Calculations for NVISITS > 1
    if nvisits != 1:
        for i in range(nvisits):
            spec = spec_noheader[2 + i]
    
            centerline = find_nearest(Lambda,calculated_point2)
            L1 = centerline - 135
            L2 = centerline - 90
            R1 = centerline + 90
            R2 = centerline + 135
                
            #generic continuum lines 35 elements wide 
            lsum= np.sum(spec[L1:L2])/ len(spec[L1:L2])
            rsum = np.sum(spec[R1:R2])/len(spec[R1:R2])
            Fc= (lsum+rsum)/2
            EqW=0
        
            if Fc!=0:
                for i in range(L2,centerline):
                    left_area = (Lambda[i+1]-Lambda[i])*(spec[i+1]-Fc)-(1./2.)*(Lambda[i+1]-Lambda[i])*(spec[i+1]-spec[i])
                    EqW += left_area
                for i in range(centerline,R1):
                    right_area = (Lambda[i+1]-Lambda[i])*(spec[i]-Fc)-(1./2.)*(Lambda[i+1]-Lambda[i])*(spec[i]-spec[i+1])
                    EqW += right_area
                EqW_rounded = round(EqW/Fc,5)
                EqW_array.append(EqW_rounded)
            
            if Fc==0:
                EqW_array.append(0)
    
#Error Calculations
    Single_StD = [] 
    avg = np.mean(EqW_array)

#Calculating the standard dev for each element
    for i in EqW_array:
        squared = (i - avg)**2
        final=round(np.sqrt(squared/len(EqW_array)),5)
        Single_StD.append(final) 
    
#Average standard dev
    StD_avg = round(np.std(EqW_array),5)
        
#Average EqW
    EqW_avg = round(np.mean(EqW_array),5)
    
    emission_dict['StD_avg'+str(11+j)]= StD_avg
    emission_dict['EqW_avg'+str(11+j)]=EqW_avg
    emission_dict['EqW_array'+str(11+j)]=EqW_array
    emission_dict['Single_StD'+str(11+j)]=Single_StD
    
    
    #values={'StD_avg'+str(11+j):StD_avg,'EqW_avg'+str(11+j):EqW_avg,'EqW_array'+str(11+j):EqW_array,
    #        'Single_StD'+str(11+j):Single_StD}
    #print(j)
    #print(values)
    #return values

In [4]:
def Brackett_Catalog(loc_id,twomass_id):
    emission_dict={}
    
#given a certain spec
    spec_header = apread.apStar(loc_id,twomass_id,ext=0,header=True)
    spec_noheader = apread.apStar(loc_id,twomass_id,ext=1,header=False)
    nvisits = spec_header[1]['NVISITS']
    emission_dict['nvisits']=nvisits
    EqW_array = []
    
    
#Getting HJD for visits
    hjd=[]
    for i in range(nvisits):
        hjd_visit = str('HJD'+str(i+1))
        hjd.append(spec_header[1][hjd_visit])
    emission_dict['HJD']=hjd
    
#Getting RA
    RA = spec_header[1]['RA']
    emission_dict['RA']=RA
    
#Getting Dec
    dec = spec_header[1]['DEC']
    emission_dict['DEC']=dec
    
#Getting J Mag
    J_mag = spec_header[1]['J']
    emission_dict['J']=J_mag
    
#Getting H Mag
    H_mag = spec_header[1]['H']
    emission_dict['H']=H_mag
    
#Getting K Mag
    K_mag = spec_header[1]['K']
    emission_dict['K']=K_mag  
    
#Getting TEffective
    Teff_avg = spec_header[1]['RVTEFF']
    Teff_single=[]
    for i in range(nvisits):
        teff_visit = str('RVTEFF'+str(i+1))
        Teff_single.append(spec_header[1][teff_visit])
    emission_dict['Teff_avg']=Teff_avg
    emission_dict['Teff_single']=Teff_single
    
#Getting LogG
    Logg_avg = spec_header[1]['RVLOGG']
    Logg_single=[]
    for i in range(nvisits):
        logg_visit = str('RVLOGG'+str(i+1))
        Logg_single.append(spec_header[1][logg_visit])
    emission_dict['LogG_avg']=Logg_avg
    emission_dict['LogG_single']=Logg_single
    
#Getting SNR
    SNR_avg = spec_header[1]['SNR']
    SNR_single=[]
    for i in range(nvisits):
        SNR_visit = str('SNRVIS'+str(i+1))
        SNR_single.append(spec_header[1][SNR_visit])
    emission_dict['SNR_avg']=SNR_avg
    emission_dict['SNR_single']=SNR_single
    
#Getting Glong
    Glon = spec_header[1]['GLON']
    emission_dict['Glon']=Glon   
    
#Getting Glat
    Glat = spec_header[1]['GLAT']
    emission_dict['Glat']=Glat
    
    for j in range(10):
        EqW_array = []
        Brackett_Equiv_Width(loc_id,twomass_id,j,EqW_array,emission_dict)
    
    return emission_dict

In [5]:
def All_Outputs(csvname,allsavefile,avgsavefile):
    
    #INPUT
    all_list=[]
    avg_list=[]
    
    with open(csvname) as csvfile:
        
        reader = csv.DictReader(csvfile,delimiter='\t')
    
        for row in reader:
            loc_id=int(row['Location ID'])
            twomass_id=row['2Mass ID']
            
            print(loc_id,twomass_id)
            value=Brackett_Catalog(loc_id,twomass_id)
            #print(value)
            
            
            for i in range(value['nvisits']):
                all_list.append((loc_id,twomass_id,i+1,value['HJD'][i],value['EqW_array11'][i],value['EqW_array12'][i],
                                value['EqW_array13'][i],value['EqW_array14'][i],value['EqW_array15'][i],value['EqW_array16'][i],
                                value['EqW_array17'][i],value['EqW_array18'][i],value['EqW_array19'][i],value['EqW_array20'][i],
                                value['Single_StD11'][i],value['Single_StD12'][i],value['Single_StD13'][i],
                                value['Single_StD14'][i],value['Single_StD15'][i],value['Single_StD16'][i],
                                value['Single_StD17'][i],value['Single_StD18'][i],value['Single_StD19'][i],
                                value['Single_StD20'][i],value['Teff_single'][i],value['LogG_single'][i],value['SNR_single'][i]))
                
            avg_list.append((loc_id,twomass_id,value['nvisits'],value['EqW_avg11'],value['EqW_avg12'],
                            value['EqW_avg13'],value['EqW_avg14'],value['EqW_avg15'],value['EqW_avg16'],
                            value['EqW_avg17'],value['EqW_avg18'],value['EqW_avg19'],value['EqW_avg20'],
                            value['StD_avg11'],value['StD_avg12'],value['StD_avg13'],value['StD_avg14'],
                            value['StD_avg15'],value['StD_avg16'],value['StD_avg17'],value['StD_avg18'],
                            value['StD_avg19'],value['StD_avg20'],value['RA'],value['DEC'],value['Glon'],value['Glat'],
                            value['J'],value['H'],value['K'],value['Teff_avg'],value['LogG_avg'],value['SNR_avg']))
    
    #Output for every visit
    with open(allsavefile,'w') as savefile:
        fieldnames = ['Location ID','2Mass ID','Visit #','HJD','Br11 EqW','Br12 EqW','Br13 EqW',
                      'Br14 EqW','Br15 EqW','Br16 EqW','Br17 EqW','Br18 EqW','Br19 EqW','Br20 EqW',
                      'Br11 STD','Br12 STD','Br13 STD','Br14 STD','Br15 STD','Br16 STD','Br17 STD',
                      'Br18 STD','Br19 STD','Br20 STD','TEFF','LOGG','SNR']
        writer = csv.DictWriter(savefile,delimiter='\t',fieldnames=fieldnames)
        
        writer.writeheader()
        for i in range(len(all_list)):
            writer.writerow({'Location ID': all_list[i][0],'2Mass ID': all_list[i][1],'Visit #': all_list[i][2],
                             'HJD': all_list[i][3],'Br11 EqW': all_list[i][4],'Br12 EqW': all_list[i][5],
                             'Br13 EqW': all_list[i][6],'Br14 EqW': all_list[i][7],'Br15 EqW': all_list[i][8],
                             'Br16 EqW': all_list[i][9],'Br17 EqW': all_list[i][10],'Br18 EqW': all_list[i][11],
                             'Br19 EqW': all_list[i][12],'Br20 EqW': all_list[i][13],'Br11 STD': all_list[i][14],
                             'Br12 STD': all_list[i][15],'Br13 STD': all_list[i][16],
                             'Br14 STD': all_list[i][17],'Br15 STD': all_list[i][18],
                             'Br16 STD': all_list[i][19],'Br17 STD': all_list[i][20],'Br18 STD': all_list[i][21],
                             'Br19 STD': all_list[i][22],'Br20 STD': all_list[i][23],'TEFF': all_list[i][24],
                             'LOGG': all_list[i][25],'SNR': all_list[i][26]})
    
    #Output for average values
    with open(avgsavefile,'w') as savefile2:
        fieldnames = ['Location ID','2Mass ID','# of Visits','Br11 Avg EqW','Br12 Avg EqW','Br13 Avg EqW','Br14 Avg EqW',
                      'Br15 Avg EqW','Br16 Avg EqW','Br17 Avg EqW','Br18 Avg EqW','Br19 Avg EqW','Br20 Avg EqW',
                      'Br11 STD','Br12 STD','Br13 STD','Br14 STD','Br15 STD','Br16 STD','Br17 STD','Br18 STD','Br19 STD',
                      'Br20 STD','RA','Dec','Glon','Glat','J','H','K','TEFF','LOGG','SNR']
        writer = csv.DictWriter(savefile2,delimiter='\t',fieldnames=fieldnames)
        
        writer.writeheader()
        for i in range(len(avg_list)):
            writer.writerow({'Location ID': avg_list[i][0],'2Mass ID': avg_list[i][1],'# of Visits': avg_list[i][2],
                             'Br11 Avg EqW': avg_list[i][3],'Br12 Avg EqW': avg_list[i][4],'Br13 Avg EqW': avg_list[i][5],
                             'Br14 Avg EqW': avg_list[i][6],'Br15 Avg EqW': avg_list[i][7],'Br16 Avg EqW': avg_list[i][8],
                             'Br17 Avg EqW': avg_list[i][9],'Br18 Avg EqW': avg_list[i][10],'Br19 Avg EqW': avg_list[i][11],
                             'Br20 Avg EqW': avg_list[i][12],'Br11 STD': avg_list[i][13],'Br12 STD': avg_list[i][14],
                             'Br13 STD': avg_list[i][15],'Br14 STD': avg_list[i][16],'Br15 STD': avg_list[i][17],
                             'Br16 STD': avg_list[i][18],'Br17 STD': avg_list[i][19],'Br18 STD': avg_list[i][20],
                             'Br19 STD': avg_list[i][21],'Br20 STD': avg_list[i][22],'RA': avg_list[i][23],
                             'Dec': avg_list[i][24],'Glon': avg_list[i][25],'Glat': avg_list[i][26],'J': avg_list[i][27],
                             'H': avg_list[i][28],'K': avg_list[i][29],'TEFF': avg_list[i][30],'LOGG': avg_list[i][31],
                             'SNR': avg_list[i][32]})

In [6]:
All_Outputs('test.csv','All Visits4.csv','Average Visits4.csv')

4102 2M21353892+4229507
4102 2M21354457+4235157
4102 2M21354474+4250256
4102 2M21354775+4233120
4102 2M21355458+4222326
4102 2M21355534+4224111
4102 2M21355686+4256151
4102 2M21355743+4245234
4102 2M21360285+4231145
4102 2M21360302+4250260
4102 2M21360555+4246043
4102 2M21360822+4225525
4102 2M21360941+4212409
4102 2M21361089+4306343
4102 2M21361159+4255425
4102 2M21361290+4216213
4102 2M21361947+4220020
4102 2M21361975+4156288
4102 2M21362389+4158414
4102 2M21362422+4223044
4102 2M21362730+4258035
4102 2M21363086+4205192
4102 2M21363278+4303344
4102 2M21363673+4310434
4102 2M21364363+4234146
4102 2M21364365+4246069
4102 2M21364477+4239053
4102 2M21365057+4224598
4102 2M21365406+4318192
4102 2M21365699+4148166
4102 2M21365711+4241383
4102 2M21365723+4313348
4102 2M21365911+4301415
4102 2M21365948+4201446
4102 2M21370114+4224396
4102 2M21370396+4204473
4102 2M21370663+4215557
4102 2M21370672+4219169
4102 2M21370757+4141129
4102 2M21371254+4209319
4102 2M21371339+4211094
4102 2M21371359+

In [ ]:
print(u'\u03C3')

In [ ]:
print(r'$\sigma$')

In [5]:
for i in range(10):
    print(11+i)

11
12
13
14
15
16
17
18
19
20
